In [ ]:
!pip install sktime

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.5/17.5 MB 65.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.7/118.7 kB 13.6 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import pandas as pd
import numpy as np
from tqdm.auto import tqdm
import random
import os

DATA_PATH = '/content/drive/MyDrive/데이콘 캐글 컴페티션/DACON_23.07_PowerConsumption/'
SEED = 42

In [ ]:
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
import sktime
from sktime.forecasting.model_selection import temporal_train_test_split
from sktime.utils.plotting import plot_series
import matplotlib.pyplot as plt
from sklearn.metrics import make_scorer
from lightgbm import early_stopping
import xgboost as xgb


In [ ]:
def _smape(true, pred):
    true = np.array(true)
    pred = np.array(pred)
    v = 2 * np.abs(pred - true) / (np.abs(pred) + np.abs(true))
    output = np.mean(v) * 100
    return output
smape = make_scorer(_smape, greater_is_better=False)

In [ ]:
def lightgbm_smape(y_true, y_pred):
    smape_val = _smape(y_true, y_pred)
    return 'SMAPE', smape_val, False

In [ ]:
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)

seed_everything(SEED) # Seed 고정

In [ ]:
train_df = pd.read_csv(f"{DATA_PATH}train_ver3.csv")
test_df = pd.read_csv(f"{DATA_PATH}test_ver3.csv")

In [ ]:
train_df.head()

In [ ]:
test_df.head()

In [ ]:
train_df = train_df.drop(columns=['date_time', 'temp', 'wind', 'hum', 'sunshine', 'solar_rad', 'type'])
test_df = test_df.drop(columns=['date_time', 'temp', 'wind', 'hum', 'type'])

In [ ]:
train_df.head()

In [ ]:
test_df.head()

In [ ]:
# 자동 변수 생성
for i in range(1, 101):
    globals()[f'train_df_{i}'] = train_df[train_df['building_num'] == i].reset_index(drop=True)
    globals()[f'test_df_{i}'] = test_df[test_df['building_num'] == i].reset_index(drop=True)

In [ ]:
# 변수 리스트 생성
train_list = []
test_list = []
for i in globals():
    if i.startswith('train_df_'):
        train_list.append(i)
    elif i.startswith('test_df_'):
        test_list.append(i)
    else:
        pass

In [ ]:
train_list

In [ ]:
test_list

In [ ]:
# 데이터셋 만들기(마지막 7일간의 데이터를 검증데이터셋으로 사용)
def make_dataset(train_df, test_df):
    train_x = train_df.iloc[:, 2:]
    train_y = train_df['power']

    test_x = test_df.iloc[:, 1:]
    return train_x, train_y, test_x

def train_test_split(train_x, train_y, test_size=168):
    y_train, y_valid, x_train, x_valid = temporal_train_test_split(y = train_y, X = train_x, test_size = test_size)
    return x_train, y_train, x_valid, y_valid


In [ ]:
# n_fold로 데이터셋 나누기
def n_fold_train_test_split(train_x, train_y, n, test_size=168, week=11):
    x_valid = train_x[test_size * (week-n-1):test_size * (week-n)]
    y_valid = train_y[test_size * (week-n-1):test_size * (week-n)]
    x_train = train_x.drop(index = list(x_valid.index))
    y_train = train_y.drop(index = list(y_valid.index))
    return x_train, y_train, x_valid, y_valid

In [ ]:
# LGBMRegressor 모델
def lgbm_predict(model, x_train, y_train, x_valid, y_valid, stopping=300, eval_metric=lightgbm_smape):
    model.fit(x_train, y_train, eval_set=[(x_train, y_train), (x_valid, y_valid)], callbacks = [early_stopping(stopping)], eval_metric=eval_metric)
    pred = model.predict(x_valid)
    pred = pd.Series(pred)
    pred.index = np.arange(y_valid.index[0], y_valid.index[-1]+1)
    plot_series(y_train, y_valid, pd.Series(pred), markers=[',' , ',', ','])
    smape_score = _smape(y_valid, pred)
    print(f"SMAPE_SCORE : {smape_score}")
    return smape_score

# test dataset 예측
def lgbm_test_predict(model, train_x, train_y, test_x):
    model.fit(train_x, train_y)
    lgbm_pred = model.predict(test_x)
    return lgbm_pred

In [ ]:
# XGBoost 모델
def xgb_smape(preds, dtrain):
    labels = dtrain.get_label()
    v = 2 * np.abs(pred - labels) / (np.abs(pred) + np.abs(labels))
    return 'xgb_smape', np.mean(v)*100

def xgb_predict(model, x_train, y_train, x_valid, y_valid, stopping=300, eval_metric=xgb_smape):
    model.fit(x_train, y_train, eval_set=[(x_train, y_train), (x_valid, y_valid)], early_stopping_rounds=stopping, eval_metric=xgb_smape)
    pred = model.predict(x_valid)
    pred = pd.Series(pred)
    pred.index = np.arange(y_valid.index[0], y_valid.index[-1]+1)
    fig, ax = plot_series(y_train, y_valid, pd.Series(pred), markers=[',' , ',', ','])
    smape_score = _smape(y_valid, pred)
    print(f"SMAPE_SCORE : {smape_score}")
    return smape_score

def xgb_test_predict(model, train_x, train_y, test_x):
    model.fit(train_x, train_y)
    xgb_pred = model.predict(test_x)
    return xgb_pred



---
### 1번 건물


In [ ]:
train_df_1.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_1['weekend'] = train_df_1['day'].isin([6]) + 0
test_df_1['weekend'] = test_df_1['day'].isin([6]) + 0

In [ ]:
# day_of_year, time 삭제
train_df_1 = train_df_1.drop(columns=['day_of_year','time'])
test_df_1 = test_df_1.drop(columns=['day_of_year','time'])



---
### 2번 건물


In [ ]:
train_df_2.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_2['weekend'] = train_df_2['day'].isin([0]) + 0
test_df_2['weekend'] = test_df_2['day'].isin([0]) + 0

In [ ]:
train_df_2 = train_df_2.drop(columns=['day_of_year', 'time'])
test_df_2 = test_df_2.drop(columns=['day_of_year', 'time'])



---
### 3번 건물


In [ ]:
train_df_3.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_3['weekend'] = train_df_3['day'].isin([0]) + 0
test_df_3['weekend'] = test_df_3['day'].isin([0]) + 0

In [ ]:
train_df_3 = train_df_3.drop(columns=['day_of_year', 'time'])
test_df_3 = test_df_3.drop(columns=['day_of_year', 'time'])



---

### 4번 건물

In [ ]:
train_df_4.head()

In [ ]:
train_df_4 = train_df_4.drop(columns=['day_of_year', 'time'])
test_df_4 = test_df_4.drop(columns=['day_of_year', 'time'])



---
### 5번 건물


In [ ]:
train_df_5.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_5['weekend'] = train_df_5['day'].isin([0, 1, 2, 3]) + 0
test_df_5['weekend'] = test_df_5['day'].isin([0, 1, 2, 3]) + 0

In [ ]:
train_df_5 = train_df_5.drop(columns=['day_of_year', 'time'])
test_df_5 = test_df_5.drop(columns=['day_of_year', 'time'])



---
### 6번 건물


In [ ]:
train_df_6.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_6['weekend'] = 0
test_df_6['weekend'] = 0

mask_train = (train_df_6['day_of_year'] == 163) | (train_df_6['day_of_year'] == 177)| (train_df_6['day_of_year'] == 191)| (train_df_6['day_of_year'] == 205)| (train_df_6['day_of_year'] == 226)
train_df_6.loc[mask_train, 'weekend'] = 1

mask_test = test_df_6['day_of_year'] == 240
test_df_6.loc[mask_test, 'weekend'] = 1


In [ ]:
train_df_6 = train_df_6.drop(columns=['day_of_year', 'time'])
test_df_6 = test_df_6.drop(columns=['day_of_year', 'time'])



---
### 7번 건물


In [ ]:
train_df_7.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_7['weekend'] = train_df_7['day'].isin([5, 6]) + 0

test_df_7['weekend'] = test_df_7['day'].isin([5, 6]) + 0

In [ ]:
train_df_7 = train_df_7.drop(columns=['day_of_year', 'time'])
test_df_7 = test_df_7.drop(columns=['day_of_year', 'time'])



---
### 8번 건물


In [ ]:
train_df_8.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_8['weekend'] = train_df_8['day'].isin([6]) + 0

test_df_8['weekend'] = test_df_8['day'].isin([6]) + 0

In [ ]:
train_df_8 = train_df_8.drop(columns=['day_of_year', 'time'])
test_df_8 = test_df_8.drop(columns=['day_of_year', 'time'])



---
### 9번 건물


In [ ]:
train_df_9.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_9['weekend'] = 0
test_df_9['weekend'] = 0

mask_train = (train_df_9['day_of_year'] == 163) | (train_df_9['day_of_year'] == 177)| (train_df_9['day_of_year'] == 191)| (train_df_9['day_of_year'] == 205)| (train_df_9['day_of_year'] == 226)
train_df_9.loc[mask_train, 'weekend'] = 1

mask_test = test_df_9['day_of_year'] == 240
test_df_9.loc[mask_test, 'weekend'] = 1


In [ ]:
train_df_9 = train_df_9.drop(columns=['day_of_year', 'time'])
test_df_9 = test_df_9.drop(columns=['day_of_year', 'time'])



---
### 10번 건물


In [ ]:
train_df_10.head()

In [ ]:
train_df_10 = train_df_10.drop(columns=['day_of_year', 'time'])
test_df_10 = test_df_10.drop(columns=['day_of_year', 'time'])



---
### 11번 건물


In [ ]:
train_df_11.head()

In [ ]:
train_df_11 = train_df_11.drop(columns=['day_of_year', 'time'])
test_df_11 = test_df_11.drop(columns=['day_of_year', 'time'])



---
### 12번 건물


In [ ]:
train_df_12.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_12['weekend'] = train_df_12['day'].isin([6]) + 0

test_df_12['weekend'] = test_df_12['day'].isin([6]) + 0

In [ ]:
train_df_12 = train_df_12.drop(columns=['day_of_year', 'time'])
test_df_12 = test_df_12.drop(columns=['day_of_year', 'time'])



---
### 13번 건물


In [ ]:
train_df_13.head()

In [ ]:
train_df_13 = train_df_13.drop(columns=['day_of_year', 'time'])
test_df_13 = test_df_13.drop(columns=['day_of_year', 'time'])



---
### 14번 건물


In [ ]:
train_df_14.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_14['weekend'] = train_df_14['day'].isin([5,6]) + 0

test_df_14['weekend'] = test_df_14['day'].isin([5,6]) + 0

In [ ]:
train_df_14 = train_df_14.drop(columns=['day_of_year', 'time'])
test_df_14 = test_df_14.drop(columns=['day_of_year', 'time'])



---
### 15번 건물


In [ ]:
train_df_15.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_15['weekend'] = train_df_15['day'].isin([5,6]) + 0

test_df_15['weekend'] = test_df_15['day'].isin([5,6]) + 0

In [ ]:
train_df_15 = train_df_15.drop(columns=['day_of_year', 'time'])
test_df_15 = test_df_15.drop(columns=['day_of_year', 'time'])



---
### 16번 건물


In [ ]:
train_df_16.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_16['weekend'] = train_df_16['day'].isin([5, 6]) + 0

test_df_16['weekend'] = test_df_16['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_16['day_of_year'] == 157) | (train_df_16['day_of_year'] == 227)
train_df_16.loc[mask, 'weekend'] = 1

In [ ]:
train_df_16 = train_df_16.drop(columns=['day_of_year', 'time'])
test_df_16 = test_df_16.drop(columns=['day_of_year', 'time'])



---
### 17번 건물

In [ ]:
train_df_17.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_17['weekend'] = train_df_17['day'].isin([5, 6]) + 0

test_df_17['weekend'] = test_df_17['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_17['day_of_year'] == 157) | (train_df_17['day_of_year'] == 227)
train_df_17.loc[mask, 'weekend'] = 1

In [ ]:
train_df_17 = train_df_17.drop(columns=['day_of_year', 'time'])
test_df_17 = test_df_17.drop(columns=['day_of_year', 'time'])



---
### 18번 건물


In [ ]:
train_df_18.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_18['weekend'] = train_df_18['day'].isin([5, 6]) + 0

test_df_18['weekend'] = test_df_18['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_18['day_of_year'] == 157) | (train_df_18['day_of_year'] == 227)
train_df_18.loc[mask, 'weekend'] = 1

In [ ]:
train_df_18 = train_df_18.drop(columns=['day_of_year', 'time'])
test_df_18 = test_df_18.drop(columns=['day_of_year', 'time'])



---
### 19번 건물


In [ ]:
train_df_19.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_19['weekend'] = train_df_19['day'].isin([5, 6]) + 0

test_df_19['weekend'] = test_df_19['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_19['day_of_year'] == 157) | (train_df_19['day_of_year'] == 227)
train_df_19.loc[mask, 'weekend'] = 1

In [ ]:
train_df_19 = train_df_19.drop(columns=['day_of_year', 'time'])
test_df_19 = test_df_19.drop(columns=['day_of_year', 'time'])



---
### 20번 건물


In [ ]:
train_df_20.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_20['weekend'] = train_df_20['day'].isin([5, 6]) + 0

test_df_20['weekend'] = test_df_20['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_20['day_of_year'] == 157) | (train_df_20['day_of_year'] == 227)
train_df_20.loc[mask, 'weekend'] = 1

In [ ]:
train_df_20 = train_df_20.drop(columns=['day_of_year', 'time'])
test_df_20 = test_df_20.drop(columns=['day_of_year', 'time'])



---
### 21번 건물


In [ ]:
train_df_21.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_21['weekend'] = train_df_21['day'].isin([5, 6]) + 0

test_df_21['weekend'] = test_df_21['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_21['day_of_year'] == 157) | (train_df_21['day_of_year'] == 227)
train_df_21.loc[mask, 'weekend'] = 1

In [ ]:
train_df_21 = train_df_21.drop(columns=['day_of_year', 'time'])
test_df_21 = test_df_21.drop(columns=['day_of_year', 'time'])



---
### 22번 건물


In [ ]:
train_df_22.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_22['weekend'] = train_df_22['day'].isin([5, 6]) + 0

test_df_22['weekend'] = test_df_22['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_22['day_of_year'] == 157) | (train_df_22['day_of_year'] == 227)
train_df_22.loc[mask, 'weekend'] = 1

In [ ]:
train_df_22 = train_df_22.drop(columns=['day_of_year', 'time'])
test_df_22 = test_df_22.drop(columns=['day_of_year', 'time'])



---
### 23번 건물


In [ ]:
train_df_23.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_23['weekend'] = train_df_23['day'].isin([5, 6]) + 0

test_df_23['weekend'] = test_df_23['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_23['day_of_year'] == 157) | (train_df_23['day_of_year'] == 227)
train_df_23.loc[mask, 'weekend'] = 1

In [ ]:
train_df_23 = train_df_23.drop(columns=['day_of_year', 'time'])
test_df_23 = test_df_23.drop(columns=['day_of_year', 'time'])



---
### 24번 건물


In [ ]:
train_df_24.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_24['weekend'] = train_df_24['day'].isin([5, 6]) + 0

test_df_24['weekend'] = test_df_24['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_24['day_of_year'] == 157) | (train_df_24['day_of_year'] == 227)
train_df_24.loc[mask, 'weekend'] = 1

In [ ]:
train_df_24 = train_df_24.drop(columns=['day_of_year', 'time'])
test_df_24 = test_df_24.drop(columns=['day_of_year', 'time'])



---
### 25번 건물


In [ ]:
train_df_25.head()

In [ ]:
# 휴무일 지정(0: 영업일, 1: 휴무일)
train_df_25['weekend'] = (train_df_25['day'] == 0) + 0

test_df_25['weekend'] = (test_df_25['day'] == 0) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_25['day_of_year'] == 157) | (train_df_25['day_of_year'] == 227)
train_df_25.loc[mask, 'weekend'] = 1

In [ ]:
train_df_25 = train_df_25.drop(columns=['day_of_year', 'time'])
test_df_25 = test_df_25.drop(columns=['day_of_year', 'time'])



---
### 26번 건물


In [ ]:
train_df_26.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_26['weekend'] = train_df_26['day'].isin([5, 6]) + 0

test_df_26['weekend'] = test_df_26['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_26['day_of_year'] == 157) | (train_df_26['day_of_year'] == 227)
train_df_26.loc[mask, 'weekend'] = 1

In [ ]:
train_df_26 = train_df_26.drop(columns=['day_of_year', 'time'])
test_df_26 = test_df_26.drop(columns=['day_of_year', 'time'])



---
### 27번 건물


In [ ]:
train_df_27.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_27['weekend'] = train_df_27['day'].isin([5, 6]) + 0

test_df_27['weekend'] = test_df_27['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_27['day_of_year'] == 157) | (train_df_27['day_of_year'] == 227)
train_df_27.loc[mask, 'weekend'] = 1

In [ ]:
train_df_27 = train_df_27.drop(columns=['day_of_year', 'time'])
test_df_27 = test_df_27.drop(columns=['day_of_year', 'time'])



---
### 28번 건물


In [ ]:
train_df_28.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_28['weekend'] = train_df_28['day'].isin([5, 6]) + 0

test_df_28['weekend'] = test_df_28['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_28['day_of_year'] == 157) | (train_df_28['day_of_year'] == 227)
train_df_28.loc[mask, 'weekend'] = 1

In [ ]:
train_df_28 = train_df_28.drop(columns=['day_of_year', 'time'])
test_df_28 = test_df_28.drop(columns=['day_of_year', 'time'])



---
### 29번 건물


In [ ]:
train_df_29.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_29['weekend'] = train_df_29['day'].isin([5, 6]) + 0

test_df_29['weekend'] = test_df_29['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_29['day_of_year'] == 157) | (train_df_29['day_of_year'] == 227)
train_df_29.loc[mask, 'weekend'] = 1

In [ ]:
train_df_29 = train_df_29.drop(columns=['day_of_year', 'time'])
test_df_29 = test_df_29.drop(columns=['day_of_year', 'time'])



---
### 30번 건물


In [ ]:
train_df_30.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_30['weekend'] = train_df_30['day'].isin([5, 6]) + 0

test_df_30['weekend'] = test_df_30['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_30['day_of_year'] == 157) | (train_df_30['day_of_year'] == 227)
train_df_30.loc[mask, 'weekend'] = 1

In [ ]:
train_df_30 = train_df_30.drop(columns=['day_of_year', 'time'])
test_df_30 = test_df_30.drop(columns=['day_of_year', 'time'])



---
### 31번 건물


In [ ]:
train_df_31.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_31['weekend'] = train_df_31['day'].isin([5, 6]) + 0

test_df_31['weekend'] = test_df_31['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_31['day_of_year'] == 157) | (train_df_31['day_of_year'] == 227)
train_df_31.loc[mask, 'weekend'] = 1

In [ ]:
train_df_31 = train_df_31.drop(columns=['day_of_year', 'time'])
test_df_31 = test_df_31.drop(columns=['day_of_year', 'time'])



---
### 32번 건물


In [ ]:
train_df_32.head()

In [ ]:
train_df_32 = train_df_32.drop(columns=['day_of_year', 'time'])
test_df_32 = test_df_32.drop(columns=['day_of_year', 'time'])



---
### 33번 건물


In [ ]:
train_df_33.head()

In [ ]:
train_df_33 = train_df_33.drop(columns=['day_of_year', 'time'])
test_df_33 = test_df_33.drop(columns=['day_of_year', 'time'])



---
### 34번 건물


In [ ]:
train_df_34.head()

In [ ]:
train_df_34 = train_df_34.drop(columns=['day_of_year', 'time'])
test_df_34 = test_df_34.drop(columns=['day_of_year', 'time'])



---
### 35번 건물


In [ ]:
train_df_35.head()

In [ ]:
train_df_35 = train_df_35.drop(columns=['day_of_year', 'time'])
test_df_35 = test_df_35.drop(columns=['day_of_year', 'time'])



---
### 36번 건물


In [ ]:
train_df_36.head()

In [ ]:
train_df_36 = train_df_36.drop(columns=['day_of_year', 'time'])
test_df_36 = test_df_36.drop(columns=['day_of_year', 'time'])



---
### 37번 건물 - 태양광


In [ ]:
train_df_37.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_37['closed'] = 0
mask = (train_df_37['day_of_year'] == 171) | (train_df_37['day_of_year'] == 192) | (train_df_37['day_of_year'] == 220)
train_df_37.loc[mask, 'closed'] = 1

test_df_37['closed'] = 0

In [ ]:
train_df_37 = train_df_37.drop(columns=['day_of_year', 'time'])
test_df_37 = test_df_37.drop(columns=['day_of_year', 'time'])



---
### 38번 건물


In [ ]:
train_df_38.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_38['closed'] = 0
mask = (train_df_38['day_of_year'] == 164) | (train_df_38['day_of_year'] == 206) | (train_df_38['day_of_year'] == 213)
train_df_38.loc[mask, 'closed'] = 1

test_df_38['closed'] = 0

In [ ]:
train_df_38 = train_df_38.drop(columns=['day_of_year', 'time'])
test_df_38 = test_df_38.drop(columns=['day_of_year', 'time'])



---
### 39번 건물


In [ ]:
train_df_39.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_39['closed'] = 0
mask = (train_df_39['day_of_year'] == 199) | (train_df_39['day_of_year'] == 220)
train_df_39.loc[mask, 'closed'] = 1

test_df_39['closed'] = 0

In [ ]:
train_df_39 = train_df_39.drop(columns=['day_of_year', 'time'])
test_df_39 = test_df_39.drop(columns=['day_of_year', 'time'])



---

### 40번 건물

In [ ]:
train_df_40.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_40['closed'] = 0
mask = (train_df_40['day_of_year'] == 171) | (train_df_40['day_of_year'] == 199) | (train_df_40['day_of_year'] == 220)
train_df_40.loc[mask, 'closed'] = 1

test_df_40['closed'] = 0

In [ ]:
train_df_40 = train_df_40.drop(columns=['day_of_year', 'time'])
test_df_40 = test_df_40.drop(columns=['day_of_year', 'time'])



---
### 41번 건물


In [ ]:
train_df_41.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_41['closed'] = 0
mask = (train_df_41['day_of_year'] == 178) | (train_df_41['day_of_year'] == 206) | (train_df_41['day_of_year'] == 220)
train_df_41.loc[mask, 'closed'] = 1

test_df_41['closed'] = 0

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_41['weekend'] = train_df_41['day'].isin([5, 6]) + 0

test_df_41['weekend'] = test_df_41['day'].isin([5, 6]) + 0

In [ ]:
train_df_41 = train_df_41.drop(columns=['day_of_year', 'time'])
test_df_41 = test_df_41.drop(columns=['day_of_year', 'time'])



---
### 42번 건물


In [ ]:
train_df_42.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_42['closed'] = 0
mask = (train_df_42['day_of_year'] == 164) | (train_df_42['day_of_year'] == 192) | (train_df_42['day_of_year'] == 234)
train_df_42.loc[mask, 'closed'] = 1

test_df_42['closed'] = 0

In [ ]:
train_df_42 = train_df_42.drop(columns=['day_of_year', 'time'])
test_df_42 = test_df_42.drop(columns=['day_of_year', 'time'])



---
### 43번 건물


In [ ]:
train_df_43.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_43['weekend'] = train_df_43['day'].isin([5, 6]) + 0

test_df_43['weekend'] = test_df_43['day'].isin([5, 6]) + 0

In [ ]:
train_df_43 = train_df_43.drop(columns=['day_of_year', 'time'])
test_df_43 = test_df_43.drop(columns=['day_of_year', 'time'])



---
### 44번 건물


In [ ]:
train_df_44.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_44['weekend'] = train_df_44['day'].isin([5, 6]) + 0

test_df_44['weekend'] = test_df_44['day'].isin([5, 6]) + 0

In [ ]:
train_df_44 = train_df_44.drop(columns=['day_of_year', 'time'])
test_df_44 = test_df_44.drop(columns=['day_of_year', 'time'])



---
### 45번 건물


In [ ]:
train_df_45.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_45['weekend'] = train_df_45['day'].isin([5, 6]) + 0

test_df_45['weekend'] = test_df_45['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_45['day_of_year'] == 157) | (train_df_45['day_of_year'] == 227)
train_df_45.loc[mask, 'weekend'] = 1

In [ ]:
train_df_45 = train_df_45.drop(columns=['day_of_year', 'time'])
test_df_45 = test_df_45.drop(columns=['day_of_year', 'time'])



---
### 46번 건물 - 태양광

In [ ]:
train_df_46.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_46['weekend'] = train_df_46['day'].isin([5, 6]) + 0

test_df_46['weekend'] = test_df_46['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_46['day_of_year'] == 157) | (train_df_46['day_of_year'] == 227)
train_df_46.loc[mask, 'weekend'] = 1

In [ ]:
train_df_46 = train_df_46.drop(columns=['day_of_year', 'time'])
test_df_46 = test_df_46.drop(columns=['day_of_year', 'time'])



---
### 47번 건물


In [ ]:
train_df_47.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_47['weekend'] = train_df_47['day'].isin([5, 6]) + 0

test_df_47['weekend'] = test_df_47['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_47['day_of_year'] == 157) | (train_df_47['day_of_year'] == 227)
train_df_47.loc[mask, 'weekend'] = 1

In [ ]:
train_df_47 = train_df_47.drop(columns=['day_of_year', 'time'])
test_df_47 = test_df_47.drop(columns=['day_of_year', 'time'])



---
### 48번 건물 - 태양광


In [ ]:
train_df_48.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_48['weekend'] = train_df_48['day'].isin([5, 6]) + 0

test_df_48['weekend'] = test_df_48['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_48['day_of_year'] == 157) | (train_df_48['day_of_year'] == 227)
train_df_48.loc[mask, 'weekend'] = 1

In [ ]:
train_df_48 = train_df_48.drop(columns=['day_of_year', 'time'])
test_df_48 = test_df_48.drop(columns=['day_of_year', 'time'])



---
### 49번 건물 - 태양광


In [ ]:
train_df_49.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_49['weekend'] = train_df_49['day'].isin([5, 6]) + 0

test_df_49['weekend'] = test_df_49['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_49['day_of_year'] == 157) | (train_df_49['day_of_year'] == 227)
train_df_49.loc[mask, 'weekend'] = 1

In [ ]:
train_df_49 = train_df_49.drop(columns=['day_of_year', 'time'])
test_df_49 = test_df_49.drop(columns=['day_of_year', 'time'])



---
### 50번 건물 - 태양광


In [ ]:
train_df_50.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_50['weekend'] = train_df_50['day'].isin([5, 6]) + 0

test_df_50['weekend'] = test_df_50['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_50['day_of_year'] == 157) | (train_df_50['day_of_year'] == 227)
train_df_50.loc[mask, 'weekend'] = 1

In [ ]:
train_df_50 = train_df_50.drop(columns=['day_of_year', 'time'])
test_df_50 = test_df_50.drop(columns=['day_of_year', 'time'])



---
### 51번 건물


In [ ]:
train_df_51.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_51['weekend'] = train_df_51['day'].isin([5, 6]) + 0

test_df_51['weekend'] = test_df_51['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_51['day_of_year'] == 157) | (train_df_51['day_of_year'] == 227)
train_df_51.loc[mask, 'weekend'] = 1

In [ ]:
train_df_51 = train_df_51.drop(columns=['day_of_year', 'time'])
test_df_51 = test_df_51.drop(columns=['day_of_year', 'time'])



---
### 52번 건물 - 태양광


In [ ]:
train_df_52.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_52['weekend'] = train_df_52['day'].isin([5, 6]) + 0

test_df_52['weekend'] = test_df_52['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_52['day_of_year'] == 157) | (train_df_52['day_of_year'] == 227)
train_df_52.loc[mask, 'weekend'] = 1

In [ ]:
train_df_52 = train_df_52.drop(columns=['day_of_year', 'time'])
test_df_52 = test_df_52.drop(columns=['day_of_year', 'time'])



---
### 53번 건물


In [ ]:
train_df_53.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_53['weekend'] = train_df_53['day'].isin([5, 6]) + 0

test_df_53['weekend'] = test_df_53['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_53['day_of_year'] == 157) | (train_df_53['day_of_year'] == 227)
train_df_53.loc[mask, 'weekend'] = 1

In [ ]:
train_df_53 = train_df_53.drop(columns=['day_of_year', 'time'])
test_df_53 = test_df_53.drop(columns=['day_of_year', 'time'])



---
### 54번 건물


In [ ]:
train_df_54.head()

In [ ]:
# 휴무일 지정(0: 영업일, 1: 휴무일)
train_df_54['weekend'] = (train_df_54['day'] == 0) + 0

test_df_54['weekend'] = (test_df_54['day'] == 0) + 0

In [ ]:
# 8월 16일, 8월 17일 휴무일로 예상.
mask = (train_df_54['day_of_year'] == 228) | (train_df_54['day_of_year'] == 229)
train_df_54.loc[mask, 'weekend'] = 1

In [ ]:
train_df_54 = train_df_54.drop(columns=['day_of_year', 'time'])
test_df_54 = test_df_54.drop(columns=['day_of_year', 'time'])



---
### 55번 건물


In [ ]:
train_df_55.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_55['weekend'] = train_df_55['day'].isin([5, 6]) + 0

test_df_55['weekend'] = test_df_55['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_55['day_of_year'] == 157) | (train_df_55['day_of_year'] == 227)
train_df_55.loc[mask, 'weekend'] = 1

In [ ]:
train_df_55 = train_df_55.drop(columns=['day_of_year', 'time'])
test_df_55 = test_df_55.drop(columns=['day_of_year', 'time'])



---
### 56번 건물


In [ ]:
train_df_56.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_56['weekend'] = train_df_56['day'].isin([5, 6]) + 0

test_df_56['weekend'] = test_df_56['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_56['day_of_year'] == 157) | (train_df_56['day_of_year'] == 227)
train_df_56.loc[mask, 'weekend'] = 1

In [ ]:
train_df_56 = train_df_56.drop(columns=['day_of_year', 'time'])
test_df_56 = test_df_56.drop(columns=['day_of_year', 'time'])



---
### 57번 건물 - 태양광


In [ ]:
train_df_57.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_57['weekend'] = train_df_57['day'].isin([5, 6]) + 0

test_df_57['weekend'] = test_df_57['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_57['day_of_year'] == 157) | (train_df_57['day_of_year'] == 227)
train_df_57.loc[mask, 'weekend'] = 1

In [ ]:
train_df_57 = train_df_57.drop(columns=['day_of_year', 'time'])
test_df_57 = test_df_57.drop(columns=['day_of_year', 'time'])



---
### 58번 건물 - 태양광


In [ ]:
train_df_58.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_58['weekend'] = train_df_58['day'].isin([5, 6]) + 0

test_df_58['weekend'] = test_df_58['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_58['day_of_year'] == 157) | (train_df_58['day_of_year'] == 227)
train_df_58.loc[mask, 'weekend'] = 1

In [ ]:
train_df_58 = train_df_58.drop(columns=['day_of_year', 'time'])
test_df_58 = test_df_58.drop(columns=['day_of_year', 'time'])



---
### 59번 건물


In [ ]:
train_df_59.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_59['weekend'] = train_df_59['day'].isin([5, 6]) + 0

test_df_59['weekend'] = test_df_59['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_59['day_of_year'] == 157) | (train_df_59['day_of_year'] == 227)
train_df_59.loc[mask, 'weekend'] = 1

In [ ]:
train_df_59 = train_df_59.drop(columns=['day_of_year', 'time'])
test_df_59 = test_df_59.drop(columns=['day_of_year', 'time'])



---
### 60번 건물 - 태양광


In [ ]:
train_df_60.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_60['weekend'] = train_df_60['day'].isin([5, 6]) + 0

test_df_60['weekend'] = test_df_60['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_60['day_of_year'] == 157) | (train_df_60['day_of_year'] == 227)
train_df_60.loc[mask, 'weekend'] = 1

In [ ]:
train_df_60 = train_df_60.drop(columns=['day_of_year', 'time'])
test_df_60 = test_df_60.drop(columns=['day_of_year', 'time'])



---
### 61번 건물


In [ ]:
train_df_61.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_61['weekend'] = train_df_61['day'].isin([5, 6]) + 0

test_df_61['weekend'] = test_df_61['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_61['day_of_year'] == 157) | (train_df_61['day_of_year'] == 227)
train_df_61.loc[mask, 'weekend'] = 1

In [ ]:
train_df_61 = train_df_61.drop(columns=['day_of_year', 'time'])
test_df_61 = test_df_61.drop(columns=['day_of_year', 'time'])



---
### 62번 건물


In [ ]:
train_df_62.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_62['weekend'] = train_df_62['day'].isin([5, 6]) + 0

test_df_62['weekend'] = test_df_62['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_62['day_of_year'] == 157) | (train_df_62['day_of_year'] == 227)
train_df_62.loc[mask, 'weekend'] = 1

In [ ]:
train_df_62 = train_df_62.drop(columns=['day_of_year', 'time'])
test_df_62 = test_df_62.drop(columns=['day_of_year', 'time'])



---
### 63번 건물


In [ ]:
train_df_63.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_63['weekend'] = train_df_63['day'].isin([5, 6]) + 0

test_df_63['weekend'] = test_df_63['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_63['day_of_year'] == 157) | (train_df_63['day_of_year'] == 227)
train_df_63.loc[mask, 'weekend'] = 1

In [ ]:
train_df_63 = train_df_63.drop(columns=['day_of_year', 'time'])
test_df_63 = test_df_63.drop(columns=['day_of_year', 'time'])



---
### 64번 건물


In [ ]:
train_df_64.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_64['weekend'] = train_df_64['day'].isin([5, 6]) + 0

test_df_64['weekend'] = test_df_64['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_64['day_of_year'] == 157) | (train_df_64['day_of_year'] == 227)
train_df_64.loc[mask, 'weekend'] = 1

In [ ]:
train_df_64 = train_df_64.drop(columns=['day_of_year', 'time'])
test_df_64 = test_df_64.drop(columns=['day_of_year', 'time'])



---
### 65번 건물


In [ ]:
train_df_65.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_65['weekend'] = train_df_65['day'].isin([5, 6]) + 0

test_df_65['weekend'] = test_df_65['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_65['day_of_year'] == 157) | (train_df_65['day_of_year'] == 227)
train_df_65.loc[mask, 'weekend'] = 1

In [ ]:
train_df_65 = train_df_65.drop(columns=['day_of_year', 'time'])
test_df_65 = test_df_65.drop(columns=['day_of_year', 'time'])



---
### 66번 건물


In [ ]:
train_df_66.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_66['weekend'] = train_df_66['day'].isin([5, 6]) + 0

test_df_66['weekend'] = test_df_66['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_66['day_of_year'] == 157) | (train_df_66['day_of_year'] == 227)
train_df_66.loc[mask, 'weekend'] = 1

In [ ]:
train_df_66 = train_df_66.drop(columns=['day_of_year', 'time'])
test_df_66 = test_df_66.drop(columns=['day_of_year', 'time'])



---
### 67번 건물


In [ ]:
train_df_67.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_67['weekend'] = train_df_67['day'].isin([5, 6]) + 0

test_df_67['weekend'] = test_df_67['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_67['day_of_year'] == 157) | (train_df_67['day_of_year'] == 227)
train_df_67.loc[mask, 'weekend'] = 1

In [ ]:
train_df_67 = train_df_67.drop(columns=['day_of_year', 'time'])
test_df_67 = test_df_67.drop(columns=['day_of_year', 'time'])



---
### 68번 건물


In [ ]:
train_df_68.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_68['weekend'] = train_df_68['day'].isin([5, 6]) + 0

test_df_68['weekend'] = test_df_68['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_68['day_of_year'] == 157) | (train_df_68['day_of_year'] == 227)
train_df_68.loc[mask, 'weekend'] = 1

In [ ]:
train_df_68 = train_df_68.drop(columns=['day_of_year', 'time'])
test_df_68 = test_df_68.drop(columns=['day_of_year', 'time'])



---
### 69번 건물


In [ ]:
train_df_69.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_69['weekend'] = train_df_69['day'].isin([5, 6]) + 0

test_df_69['weekend'] = test_df_69['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_69['day_of_year'] == 157) | (train_df_69['day_of_year'] == 227)
train_df_69.loc[mask, 'weekend'] = 1

In [ ]:
train_df_69 = train_df_69.drop(columns=['day_of_year', 'time'])
test_df_69 = test_df_69.drop(columns=['day_of_year', 'time'])



---
### 70번 건물


In [ ]:
train_df_70.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_70['weekend'] = train_df_70['day'].isin([5, 6]) + 0

test_df_70['weekend'] = test_df_70['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_70['day_of_year'] == 157) | (train_df_70['day_of_year'] == 227)
train_df_70.loc[mask, 'weekend'] = 1

In [ ]:
train_df_70 = train_df_70.drop(columns=['day_of_year', 'time'])
test_df_70 = test_df_70.drop(columns=['day_of_year', 'time'])



---
### 71번 건물


In [ ]:
train_df_71.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_71['weekend'] = train_df_71['day'].isin([5, 6]) + 0

test_df_71['weekend'] = test_df_71['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_71['day_of_year'] == 157) | (train_df_71['day_of_year'] == 227)
train_df_71.loc[mask, 'weekend'] = 1

In [ ]:
train_df_71 = train_df_71.drop(columns=['day_of_year', 'time'])
test_df_71 = test_df_71.drop(columns=['day_of_year', 'time'])



---

### 72번 건물

In [ ]:
train_df_72.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_72['weekend'] = train_df_72['day'].isin([5, 6]) + 0

test_df_72['weekend'] = test_df_72['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_72['day_of_year'] == 157) | (train_df_72['day_of_year'] == 227)
train_df_72.loc[mask, 'weekend'] = 1

In [ ]:
train_df_72 = train_df_72.drop(columns=['day_of_year', 'time'])
test_df_72 = test_df_72.drop(columns=['day_of_year', 'time'])



---
### 73번 건물


In [ ]:
train_df_73.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_73['weekend'] = train_df_73['day'].isin([5, 6]) + 0

test_df_73['weekend'] = test_df_73['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_73['day_of_year'] == 157) | (train_df_73['day_of_year'] == 227)
train_df_73.loc[mask, 'weekend'] = 1

In [ ]:
train_df_73 = train_df_73.drop(columns=['day_of_year', 'time'])
test_df_73 = test_df_73.drop(columns=['day_of_year', 'time'])



---
### 74번 건물


In [ ]:
train_df_74.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_74['weekend'] = train_df_74['day'].isin([5, 6]) + 0

test_df_74['weekend'] = test_df_74['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_74['day_of_year'] == 157) | (train_df_74['day_of_year'] == 227)
train_df_74.loc[mask, 'weekend'] = 1

In [ ]:
train_df_74 = train_df_74.drop(columns=['day_of_year', 'time'])
test_df_74 = test_df_74.drop(columns=['day_of_year', 'time'])



---
### 75번 건물


In [ ]:
train_df_75.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_75['weekend'] = train_df_75['day'].isin([5, 6, 0]) + 0

test_df_75['weekend'] = test_df_75['day'].isin([5, 6, 0]) + 0

In [ ]:
train_df_75 = train_df_75.drop(columns=['day_of_year', 'time'])
test_df_75 = test_df_75.drop(columns=['day_of_year', 'time'])



---
### 76번 건물


In [ ]:
train_df_76.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_76['weekend'] = train_df_76['day'].isin([5, 6]) + 0

test_df_76['weekend'] = test_df_76['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_76['day_of_year'] == 157) | (train_df_76['day_of_year'] == 227)
train_df_76.loc[mask, 'weekend'] = 1

In [ ]:
train_df_76 = train_df_76.drop(columns=['day_of_year', 'time'])
test_df_76 = test_df_76.drop(columns=['day_of_year', 'time'])



---
### 77번 건물


In [ ]:
train_df_77.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_77['weekend'] = train_df_77['day'].isin([5, 6]) + 0

test_df_77['weekend'] = test_df_77['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_77['day_of_year'] == 157) | (train_df_77['day_of_year'] == 227)
train_df_77.loc[mask, 'weekend'] = 1

In [ ]:
train_df_77 = train_df_77.drop(columns=['day_of_year', 'time'])
test_df_77 = test_df_77.drop(columns=['day_of_year', 'time'])



---
### 78번 건물

In [ ]:
train_df_78.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_78['weekend'] = train_df_78['day'].isin([5, 6]) + 0

test_df_78['weekend'] = test_df_78['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_78['day_of_year'] == 157) | (train_df_78['day_of_year'] == 227)
train_df_78.loc[mask, 'weekend'] = 1

In [ ]:
train_df_78 = train_df_78.drop(columns=['day_of_year', 'time'])
test_df_78 = test_df_78.drop(columns=['day_of_year', 'time'])



---
### 79번 건물


In [ ]:
train_df_79.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_79['weekend'] = train_df_79['day'].isin([5, 6]) + 0

test_df_79['weekend'] = test_df_79['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_79['day_of_year'] == 157) | (train_df_79['day_of_year'] == 227)
train_df_79.loc[mask, 'weekend'] = 1

In [ ]:
train_df_79 = train_df_79.drop(columns=['day_of_year', 'time'])
test_df_79 = test_df_79.drop(columns=['day_of_year', 'time'])



---
### 80번 건물


In [ ]:
train_df_80.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_80['weekend'] = train_df_80['day'].isin([5, 6]) + 0

test_df_80['weekend'] = test_df_80['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_80['day_of_year'] == 157) | (train_df_80['day_of_year'] == 227)
train_df_80.loc[mask, 'weekend'] = 1

In [ ]:
train_df_80 = train_df_80.drop(columns=['day_of_year', 'time'])
test_df_80 = test_df_80.drop(columns=['day_of_year', 'time'])



---
### 81번 건물


In [ ]:
train_df_81.head()

In [ ]:
train_df_81 = train_df_81.drop(columns=['day_of_year', 'time'])
test_df_81 = test_df_81.drop(columns=['day_of_year', 'time'])



---
### 82번 건물


In [ ]:
train_df_82.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_82['weekend'] = train_df_82['day'].isin([5, 6]) + 0

test_df_82['weekend'] = test_df_82['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_82['day_of_year'] == 157) | (train_df_82['day_of_year'] == 227)
train_df_82.loc[mask, 'weekend'] = 1

In [ ]:
train_df_82 = train_df_82.drop(columns=['day_of_year', 'time'])
test_df_82 = test_df_82.drop(columns=['day_of_year', 'time'])



---
### 83번 건물


In [ ]:
train_df_83.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_83['weekend'] = train_df_83['day'].isin([5, 6]) + 0

test_df_83['weekend'] = test_df_83['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_83['day_of_year'] == 157) | (train_df_83['day_of_year'] == 227)
train_df_83.loc[mask, 'weekend'] = 1

In [ ]:
train_df_83 = train_df_83.drop(columns=['day_of_year', 'time'])
test_df_83 = test_df_83.drop(columns=['day_of_year', 'time'])



---
### 84번 건물


In [ ]:
train_df_84.head()

In [ ]:
# 주말 지정(0: 주중, 1: 주말)
train_df_84['weekend'] = train_df_84['day'].isin([5, 6]) + 0

test_df_84['weekend'] = test_df_84['day'].isin([5, 6]) + 0

In [ ]:
# 공휴일 주말로 지정(공휴일이 2일 밖에 존재하지 않으며, 주말과 차이가 없다고 판단)
mask = (train_df_84['day_of_year'] == 157) | (train_df_84['day_of_year'] == 227)
train_df_84.loc[mask, 'weekend'] = 1

In [ ]:
train_df_84 = train_df_84.drop(columns=['day_of_year', 'time'])
test_df_84 = test_df_84.drop(columns=['day_of_year', 'time'])



---
### 85번 건물


In [ ]:
train_df_85.head()

In [ ]:
train_df_85 = train_df_85.drop(columns=['day_of_year', 'time'])
test_df_85 = test_df_85.drop(columns=['day_of_year', 'time'])



---
### 86번 건물


In [ ]:
train_df_86.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_86['weekend'] = 0
test_df_86['weekend'] = 0

mask_train = (train_df_86['day_of_year'] == 161) | (train_df_86['day_of_year'] == 177)| (train_df_86['day_of_year'] == 191)| (train_df_86['day_of_year'] == 205)| (train_df_86['day_of_year'] == 222)
train_df_86.loc[mask_train, 'weekend'] = 1

In [ ]:
train_df_86 = train_df_86.drop(columns=['day_of_year', 'time'])
test_df_86 = test_df_86.drop(columns=['day_of_year', 'time'])



---
### 87번 건물


In [ ]:
train_df_87.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_87['weekend'] = 0
test_df_87['weekend'] = 0

mask_train = (train_df_87['day_of_year'] == 163) | (train_df_87['day_of_year'] == 177)| (train_df_87['day_of_year'] == 191)| (train_df_87['day_of_year'] == 205)| (train_df_87['day_of_year'] == 226)
train_df_87.loc[mask_train, 'weekend'] = 1

mask_test = test_df_87['day_of_year'] == 240
test_df_87.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_87 = train_df_87.drop(columns=['day_of_year', 'time'])
test_df_87 = test_df_87.drop(columns=['day_of_year', 'time'])



---
### 88번 건물


In [ ]:
train_df_88.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_88['weekend'] = 0
test_df_88['weekend'] = 0

mask_train = (train_df_88['day_of_year'] == 163) | (train_df_88['day_of_year'] == 177)| (train_df_88['day_of_year'] == 191)| (train_df_88['day_of_year'] == 205)| (train_df_88['day_of_year'] == 226)
train_df_88.loc[mask_train, 'weekend'] = 1

mask_test = test_df_88['day_of_year'] == 240
test_df_88.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_88 = train_df_88.drop(columns=['day_of_year', 'time'])
test_df_88 = test_df_88.drop(columns=['day_of_year', 'time'])



---
### 89번 건물


In [ ]:
train_df_89.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_89['weekend'] = 0
test_df_89['weekend'] = 0

mask_train = (train_df_89['day_of_year'] == 163) | (train_df_89['day_of_year'] == 177)| (train_df_89['day_of_year'] == 191)| (train_df_89['day_of_year'] == 205)| (train_df_89['day_of_year'] == 226)
train_df_89.loc[mask_train, 'weekend'] = 1

mask_test = test_df_89['day_of_year'] == 240
test_df_89.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_89 = train_df_89.drop(columns=['day_of_year', 'time'])
test_df_89 = test_df_89.drop(columns=['day_of_year', 'time'])



---
### 90번 건물


In [ ]:
train_df_90.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_90['weekend'] = 0
test_df_90['weekend'] = 0

mask_train = (train_df_90['day_of_year'] == 163) | (train_df_90['day_of_year'] == 177)| (train_df_90['day_of_year'] == 191)| (train_df_90['day_of_year'] == 205)| (train_df_90['day_of_year'] == 226)
train_df_90.loc[mask_train, 'weekend'] = 1

mask_test = test_df_90['day_of_year'] == 240
test_df_90.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_90 = train_df_90.drop(columns=['day_of_year', 'time'])
test_df_90 = test_df_90.drop(columns=['day_of_year', 'time'])



---
### 91번 건물


In [ ]:
train_df_91.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_91['weekend'] = 0
test_df_91['weekend'] = 0

mask_train = (train_df_91['day_of_year'] == 163) | (train_df_91['day_of_year'] == 177)| (train_df_91['day_of_year'] == 191)| (train_df_91['day_of_year'] == 205)| (train_df_91['day_of_year'] == 226)
train_df_91.loc[mask_train, 'weekend'] = 1

mask_test = test_df_91['day_of_year'] == 240
test_df_91.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_91 = train_df_91.drop(columns=['day_of_year', 'time'])
test_df_91 = test_df_91.drop(columns=['day_of_year', 'time'])



---
### 92번 건물

In [ ]:
train_df_92.head()

In [ ]:
# 휴무일 지정(1: 휴무일, 0: 영업일)
train_df_92['weekend'] = 0
test_df_92['weekend'] = 0

mask_train = (train_df_92['day_of_year'] == 163) | (train_df_92['day_of_year'] == 177)| (train_df_92['day_of_year'] == 191)| (train_df_92['day_of_year'] == 205)| (train_df_92['day_of_year'] == 226)
train_df_92.loc[mask_train, 'weekend'] = 1

mask_test = test_df_92['day_of_year'] == 240
test_df_92.loc[mask_test, 'weekend'] = 1

In [ ]:
train_df_92 = train_df_92.drop(columns=['day_of_year', 'time'])
test_df_92 = test_df_92.drop(columns=['day_of_year', 'time'])



---
### 93번 건물


In [ ]:
train_df_93.head()

In [ ]:
train_df_93 = train_df_93.drop(columns=['day_of_year', 'time'])
test_df_93 = test_df_93.drop(columns=['day_of_year', 'time'])



---
### 94번 건물


In [ ]:
train_df_94.head()

In [ ]:
train_df_94 = train_df_94.drop(columns=['day_of_year', 'time'])
test_df_94 = test_df_94.drop(columns=['day_of_year', 'time'])



---
### 95번 건물


In [ ]:
train_df_95.head()

In [ ]:
train_df_95 = train_df_95.drop(columns=['day_of_year', 'time'])
test_df_95 = test_df_95.drop(columns=['day_of_year', 'time'])



---
### 96번 건물


In [ ]:
train_df_96.head()

In [ ]:
train_df_96 = train_df_96.drop(columns=['day_of_year', 'time'])
test_df_96 = test_df_96.drop(columns=['day_of_year', 'time'])



---
### 97번 건물


In [ ]:
train_df_97.head()

In [ ]:
train_df_97 = train_df_97.drop(columns=['day_of_year', 'time'])
test_df_97 = test_df_97.drop(columns=['day_of_year', 'time'])



---
### 98번 건물


In [ ]:
train_df_98.head()

In [ ]:
train_df_98 = train_df_98.drop(columns=['day_of_year', 'time'])
test_df_98 = test_df_98.drop(columns=['day_of_year', 'time'])



---
### 99번 건물


In [ ]:
train_df_99.head()

In [ ]:
train_df_99 = train_df_99.drop(columns=['day_of_year', 'time'])
test_df_99 = test_df_99.drop(columns=['day_of_year', 'time'])



---
### 100번 건물


In [ ]:
train_df_100.head()

In [ ]:
train_df_100 = train_df_100.drop(columns=['day_of_year', 'time'])
test_df_100 = test_df_100.drop(columns=['day_of_year', 'time'])

## 건물별 예측 실행

In [ ]:
# LGBM 모델 사용
lgbm_preds = np.array([])
fold = 4
smape_score_mean = []

def lgbm_evaluation(train_ft, test_ft) :
    global lgbm_preds

    model = LGBMRegressor(random_state=SEED, objective='regression')
    train_x, train_y, test_x = make_dataset(eval(train_df), eval(test_df))
    # 건물별 fold별 smape score
    smape_score = []
    for n in tqdm(range(fold)):
        x_train, y_train, x_valid, y_valid = n_fold_train_test_split(train_x, train_y, n=n)

        model.fit(x_train, y_train, eval_set=[(x_valid, y_valid)], callbacks = [early_stopping(120)], eval_metric=lightgbm_smape)

        pred = model.predict(x_valid)
        score = _smape(y_valid, pred)
        smape_score.append(score)

    smape_score_mean.append(np.mean(smape_score))

    lgbm_pred = lgbm_test_predict(model, train_x, train_y, test_x)
    lgbm_preds = np.concatenate([lgbm_preds, lgbm_pred])

print(smape_score_mean)

In [ ]:
lgbm_preds.shape

(16800,)

In [ ]:
# XGBoost 모델 사용
xgb_preds = np.array([])
fold = 4
smape_score_mean = []
for train_df, test_df in tqdm(zip(train_list, test_list), total=100):
    model = XGBRegressor(random_state=SEED, n_jobs=-1, verbosity=0)
    train_x, train_y, test_x = make_dataset(eval(train_df), eval(test_df))
    # 건물별 fold별 smape score
    smape_score = []
    for n in tqdm(range(fold)):
        x_train, y_train, x_valid, y_valid = n_fold_train_test_split(train_x, train_y, n=n)

        model.fit(x_train, y_train, eval_set=[(x_train, y_train), (x_valid, y_valid)], early_stopping_rounds=60, eval_metric=xgb_smape)

        pred = model.predict(x_valid)
        score = _smape(y_valid, pred)
        smape_score.append(score)

    smape_score_mean.append(np.mean(smape_score))

    xgb_pred = xgb_test_predict(model, train_x, train_y, test_x)
    xgb_preds = np.concatenate([xgb_preds, xgb_pred])

print(smape_score_mean)

  0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

[0]	validation_0-rmse:2067.13689	validation_0-xgb_smape:53.79177	validation_1-rmse:2123.27719	validation_1-xgb_smape:53.87237
[1]	validation_0-rmse:1460.54158	validation_0-xgb_smape:32.46268	validation_1-rmse:1484.15128	validation_1-xgb_smape:32.28402
[2]	validation_0-rmse:1036.90080	validation_0-xgb_smape:20.69094	validation_1-rmse:1038.21263	validation_1-xgb_smape:20.53557
[3]	validation_0-rmse:741.00364	validation_0-xgb_smape:13.67565	validation_1-rmse:738.35894	validation_1-xgb_smape:13.71912
[4]	validation_0-rmse:534.50032	validation_0-xgb_smape:9.25464	validation_1-rmse:530.88754	validation_1-xgb_smape:9.32753
[5]	validation_0-rmse:390.84816	validation_0-xgb_smape:6.36191	validation_1-rmse:385.61704	validation_1-xgb_smape:6.32594
[6]	validation_0-rmse:291.54215	validation_0-xgb_smape:4.51629	validation_1-rmse:294.75894	validation_1-xgb_smape:4.46485
[7]	validation_0-rmse:224.57891	validation_0-xgb_smape:3.33226	validation_1-rmse:241.81217	validation_1-xgb_smape:3.39172
[8]	valida

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[12]	validation_0-rmse:104.90660	validation_0-xgb_smape:1.54450	validation_1-rmse:186.98331	validation_1-xgb_smape:2.77829
[13]	validation_0-rmse:98.74977	validation_0-xgb_smape:1.46728	validation_1-rmse:187.78912	validation_1-xgb_smape:2.80638
[14]	validation_0-rmse:94.29546	validation_0-xgb_smape:1.39879	validation_1-rmse:187.01223	validation_1-xgb_smape:2.79797
[15]	validation_0-rmse:90.86784	validation_0-xgb_smape:1.35802	validation_1-rmse:187.23838	validation_1-xgb_smape:2.82282
[16]	validation_0-rmse:86.77122	validation_0-xgb_smape:1.28720	validation_1-rmse:187.72644	validation_1-xgb_smape:2.79574
[17]	validation_0-rmse:85.53568	validation_0-xgb_smape:1.27036	validation_1-rmse:187.83068	validation_1-xgb_smape:2.80285
[18]	validation_0-rmse:84.14528	validation_0-xgb_smape:1.25347	validation_1-rmse:187.91878	validation_1-xgb_smape:2.80916
[19]	validation_0-rmse:82.06514	validation_0-xgb_smape:1.22450	validation_1-rmse:187.98139	validation_1-xgb_smape:2.81320
[20]	validation_0-rmse:

...

[8]	validation_0-rmse:53.66872	validation_0-xgb_smape:2.45415	validation_1-rmse:83.38429	validation_1-xgb_smape:3.44730
[9]	validation_0-rmse:44.43327	validation_0-xgb_smape:1.98022	validation_1-rmse:80.91338	validation_1-xgb_smape:3.20643
[10]	validation_0-rmse:38.77785	validation_0-xgb_smape:1.70108	validation_1-rmse:75.38859	validation_1-xgb_smape:2.97224
[11]	validation_0-rmse:35.03883	validation_0-xgb_smape:1.54419	validation_1-rmse:71.70548	validation_1-xgb_smape:2.80298
[12]	validation_0-rmse:32.76249	validation_0-xgb_smape:1.45582	validation_1-rmse:69.30094	validation_1-xgb_smape:2.68356
[13]	validation_0-rmse:31.03183	validation_0-xgb_smape:1.36036	validation_1-rmse:67.59204	validation_1-xgb_smape:2.63082
[14]	validation_0-rmse:29.14973	validation_0-xgb_smape:1.28660	validation_1-rmse:65.82437	validation_1-xgb_smape:2.58033
[15]	validation_0-rmse:28.22721	validation_0-xgb_smape:1.25212	validation_1-rmse:64.42647	validation_1-xgb_smape:2.53075
[16]	validation_0-rmse:27.63267	va

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-rmse:624.55957	validation_0-xgb_smape:53.75971	validation_1-rmse:701.71871	validation_1-xgb_smape:55.96361
[1]	validation_0-rmse:441.08191	validation_0-xgb_smape:32.39270	validation_1-rmse:511.77759	validation_1-xgb_smape:35.49048
[2]	validation_0-rmse:312.85162	validation_0-xgb_smape:20.67092	validation_1-rmse:372.35632	validation_1-xgb_smape:23.54578
[3]	validation_0-rmse:223.44007	validation_0-xgb_smape:13.65042	validation_1-rmse:275.09791	validation_1-xgb_smape:16.09531
[4]	validation_0-rmse:161.11177	validation_0-xgb_smape:9.21198	validation_1-rmse:203.13286	validation_1-xgb_smape:11.06052
[5]	validation_0-rmse:117.63527	validation_0-xgb_smape:6.33480	validation_1-rmse:176.38789	validation_1-xgb_smape:8.94149
[6]	validation_0-rmse:87.55942	validation_0-xgb_smape:4.45899	validation_1-rmse:140.03373	validation_1-xgb_smape:6.56893
[7]	validation_0-rmse:67.30301	validation_0-xgb_smape:3.24058	validation_1-rmse:115.93341	validation_1-xgb_smape:5.30446
[8]	validation_0-

/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/sklearn.py:835: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[9]	validation_0-rmse:44.80137	validation_0-xgb_smape:2.06213	validation_1-rmse:85.04257	validation_1-xgb_smape:4.73347
[10]	validation_0-rmse:39.47054	validation_0-xgb_smape:1.78514	validation_1-rmse:82.96336	validation_1-xgb_smape:4.54004
[11]	validation_0-rmse:35.86170	validation_0-xgb_smape:1.61150	validation_1-rmse:79.41154	validation_1-xgb_smape:4.34364
[12]	validation_0-rmse:33.48359	validation_0-xgb_smape:1.49627	validation_1-rmse:76.58148	validation_1-xgb_smape:4.20392
[13]	validation_0-rmse:31.52693	validation_0-xgb_smape:1.42499	validation_1-rmse:75.45795	validation_1-xgb_smape:4.12282
[14]	validation_0-rmse:29.11989	validation_0-xgb_smape:1.30817	validation_1-rmse:75.09410	validation_1-xgb_smape:4.08170
[15]	validation_0-rmse:27.51347	validation_0-xgb_smape:1.25439	validation_1-rmse:74.15232	validation_1-xgb_smape:3.93605
[16]	validation_0-rmse:26.97091	validation_0-xgb_smape:1.23529	validation_1-rmse:73.54173	validation_1-xgb_smape:3.88980
[17]	validation_0-rmse:26.22876	v

In [ ]:
np.mean(smape_score_mean)

2.901456119935818

In [ ]:
xgb_preds.shape

## 예측값 저장

In [ ]:
submission = pd.read_csv(f"{DATA_PATH}sample_submission.csv")

In [ ]:
submission.shape

In [ ]:
submission['answer']= lgbm_preds

In [ ]:
submission.to_csv(f"{DATA_PATH}LGBM_submission_ver3.csv", index=False)

In [ ]:
submission['answer'] = xgb_preds

In [ ]:
submission.to_csv(f"{DATA_PATH}XGB_submission_ver3.csv", index=False)